In [620]:
import os
import datetime
import warnings
import polars as pl
import pandas as pd
import altair as alt

from src.najdi_rok import najdi_rok
from src.pocet_stran import pocet_stran
from src.bez_bordelu import bez_bordelu
from src.alt_friendly import alt_friendly
from src.hezke_jmeno import hezke_jmeno
from src.kristi_promin import kristi_promin
from src.zjisti_vazbu import zjisti_vazbu

pl.Config(tbl_rows=100)
alt.data_transformers.disable_max_rows()
alt.themes.register('irozhlas', kristi_promin)
alt.themes.enable('irozhlas')
warnings.filterwarnings('ignore')

In [621]:
df = pl.read_parquet(os.path.join("data/cnb_sloupce","100.parquet"))
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","leader.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","008.parquet")), left_on="001", right_on="001", how="left")
df = df.to_pandas()
df = df[df["leader"].str[6].isin(["a", "t"])]
df = df[~df["leader"].str[7].isin(["b", "i", "s", " "])]
df = df[(df["008"].str[15:17] == "xr") & (df["008"].str[35:38] == "cze")]
df = pl.from_pandas(df)
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","020.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","022.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","245.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","300.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","655.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","700.parquet")), left_on="001", right_on="001", how="left")
df = df.explode("022_a").filter(pl.col("022_a").is_null())
df = df.with_columns(pl.col('008').map_elements(najdi_rok, return_dtype=int).alias('rok'))
df = df.with_columns(pl.col('300_a').map_elements(pocet_stran, return_dtype=int).alias('stran'))
df = df.with_columns(pl.col('245_a').map_elements(bez_bordelu, return_dtype=str))
df = df.explode("020_q").with_columns(pl.col("020_q").map_elements(zjisti_vazbu, return_dtype=str).alias('vazba'))
df = df.explode('245_p').with_columns(pl.col('245_p').map_elements(bez_bordelu, return_dtype=str))
print(len(df))
df = df.filter(pl.col("rok") >= 2000)

df = df.filter((~pl.col("245_h").str.contains("grafika")) | pl.col("245_h").is_null()).unique(subset=["008","100_a","245_a","245_p"], keep="first")
print(len(df))

794838
294524


In [622]:
df = df.filter(pl.col("rok") <= 2024)

In [623]:
bestsellery = pd.read_json(os.path.join("data","sckn_zebricky.json"))
bestsellery = pl.from_pandas(bestsellery)
bestsellery
isbn_bestselleru = set(bestsellery.select(pl.col("sckn_isbn")).to_series().to_list())
df_isbn = df.explode("020_a").drop_nulls(subset=['020_a']).with_columns(pl.col("020_a").map_elements(lambda x: x.replace('-','')).alias("isbn"))

In [624]:
df.sample(20)

shape: (20, 74)
┌──────────┬──────────────────────────────┬────────────────┬────────────────┬───┬───────────┬──────┬───────┬───────────┐
│ 100_ind1 ┆ 100_a                        ┆ 100_7          ┆ 100_4          ┆ … ┆ 700_g     ┆ rok  ┆ stran ┆ vazba     │
│ ---      ┆ ---                          ┆ ---            ┆ ---            ┆   ┆ ---       ┆ ---  ┆ ---   ┆ ---       │
│ str      ┆ str                          ┆ str            ┆ list[str]      ┆   ┆ list[str] ┆ i64  ┆ i64   ┆ str       │
╞══════════╪══════════════════════════════╪════════════════╪════════════════╪═══╪═══════════╪══════╪═══════╪═══════════╡
│ 1        ┆ Haran, Elizabeth,            ┆ xx0017352      ┆ ["aut"]        ┆ … ┆ null      ┆ 2016 ┆ 392   ┆ pevná     │
│ 1        ┆ Maněnová, Martina,           ┆ ola20040225001 ┆ ["aut"]        ┆ … ┆ null      ┆ 2009 ┆ 134   ┆ brožovaná │
│ 1        ┆ Collier, Paul,               ┆ pna2005311743  ┆ ["aut"]        ┆ … ┆ null      ┆ 2017 ┆ 258   ┆ pevná     │
│ 1        ┆ Jenka, Petr                  ┆ mzk20231197374 ┆ ["aut"]        ┆ … ┆ null      ┆ 2023 ┆ 239   ┆ brožovaná │
│ 1        ┆ Vágner, Karel,               ┆ jn19990209971  ┆ ["aut"]        ┆ … ┆ null      ┆ 2016 ┆ 156   ┆ pevná     │
│ 1        ┆ Cinger, František,           ┆ jn20010523018  ┆ ["aut"]        ┆ … ┆ null      ┆ 2006 ┆ 247   ┆ pevná     │
│ 1        ┆ Lukeš, Jan,                  ┆ jk01072622     ┆ ["ivr", "com"] ┆ … ┆ null      ┆ 2005 ┆ 313   ┆ pevná     │
│ 1        ┆ Varis, Lee                   ┆ mzk2007430875  ┆ ["aut"]        ┆ … ┆ null      ┆ 2007 ┆ 414   ┆ brožovaná │
│ 1        ┆ Nepil, František,            ┆ jk01083177     ┆ ["aut"]        ┆ … ┆ null      ┆ 2001 ┆ 91    ┆ pevná     │
│ 1        ┆ Rankov, Pavol,               ┆ jo2002112279   ┆ ["aut"]        ┆ … ┆ null      ┆ 2019 ┆ 322   ┆ pevná     │
│ 1        ┆ Radke, Reinhard,             ┆ xx0002374      ┆ ["aut"]        ┆ … ┆ null      ┆ 2002 ┆ 288   ┆ pevná     │
│ 1        ┆ Chaloupek, Václav,           ┆ jn20000710018  ┆ ["aut"]        ┆ … ┆ null      ┆ 2017 ┆ 363   ┆ brožovaná │
│ 1        ┆ Yarros, Rebecca              ┆ xx0306981      ┆ ["aut"]        ┆ … ┆ null      ┆ 2024 ┆ 385   ┆ brožovaná │
│ 1        ┆ Valognes, Aurélie,           ┆ xx0250217      ┆ ["aut"]        ┆ … ┆ null      ┆ 2020 ┆ 294   ┆ pevná     │
│ 1        ┆ Kremláček, Josef,            ┆ jn19990209425  ┆ ["art"]        ┆ … ┆ null      ┆ 2002 ┆ 8     ┆ null      │
│ 1        ┆ Grimmichová, Alena Isabella, ┆ js20050411008  ┆ ["aut"]        ┆ … ┆ null      ┆ 2013 ┆ 158   ┆ pevná     │
│ 1        ┆ Birkner-Mahler, Frieda,      ┆ jn20000600873  ┆ ["aut"]        ┆ … ┆ null      ┆ 2010 ┆ 221   ┆ pevná     │
│ 1        ┆ Hejda, Jan,                  ┆ nlk20010096776 ┆ ["aut"]        ┆ … ┆ null      ┆ 2008 ┆ 1     ┆ null      │
│ 1        ┆ Vincenz, Stanisław,          ┆ jo2002102395   ┆ ["aut"]        ┆ … ┆ null      ┆ 2021 ┆ 608   ┆ brožovaná │
│ 1        ┆ Brydak, Piotr                ┆ mzk2015874488  ┆ ["ill"]        ┆ … ┆ null      ┆ 2020 ┆ 10    ┆ brožovaná │
└──────────┴──────────────────────────────┴────────────────┴────────────────┴───┴───────────┴──────┴───────┴───────────┘

In [625]:
def zjisti_vysku(c300):
    import re
    try:
        return int(re.search('\d{1,3}', str(c300)).group())
    except:
        pass

In [626]:
df = df.explode('300_c').with_columns(pl.col('300_c').map_elements(zjisti_vysku).alias('vyska'))

## Vazby

In [628]:
def podil_vazeb(frejm):
    vazby = frejm.filter(pl.col("vazba") == 'brožovaná').group_by("rok").len().sort(by="rok").rename({"len":"brožovaná"})
    vazby = vazby.join(df.filter(pl.col("vazba").is_in(['brožovaná','pevná'])).group_by("rok").len().sort(by="rok").rename({"len":"jakákoliv"}), left_on="rok", right_on="rok", how="left")
    vazby = vazby.join(df.group_by("rok").len().sort(by="rok").rename({"len":"vše"}), left_on="rok", right_on="rok", how="left")
    vazby = vazby.with_columns((pl.col("brožovaná") / pl.col("jakákoliv")).alias("podíl"))
    vazby = vazby.with_columns((pl.col("jakákoliv") / pl.col("vše")).alias("vyplněnost"))
    return vazby

In [629]:
podil_vazeb(df)

shape: (25, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 2000 ┆ 5255      ┆ 8282      ┆ 10141 ┆ 0.634509 ┆ 0.816685   │
│ 2001 ┆ 5344      ┆ 8325      ┆ 10095 ┆ 0.641922 ┆ 0.824666   │
│ 2002 ┆ 5247      ┆ 8417      ┆ 10210 ┆ 0.623381 ┆ 0.824388   │
│ 2003 ┆ 5257      ┆ 8916      ┆ 10595 ┆ 0.589614 ┆ 0.841529   │
│ 2004 ┆ 5361      ┆ 9247      ┆ 10956 ┆ 0.579756 ┆ 0.844012   │
│ 2005 ┆ 5830      ┆ 9783      ┆ 11305 ┆ 0.595932 ┆ 0.865369   │
│ 2006 ┆ 6085      ┆ 10299     ┆ 11929 ┆ 0.590834 ┆ 0.863358   │
│ 2007 ┆ 6358      ┆ 10717     ┆ 12653 ┆ 0.593263 ┆ 0.846993   │
│ 2008 ┆ 6398      ┆ 11289     ┆ 13186 ┆ 0.566746 ┆ 0.856135   │
│ 2009 ┆ 6034      ┆ 10710     ┆ 12386 ┆ 0.563399 ┆ 0.864686   │
│ 2010 ┆ 6160      ┆ 10991     ┆ 12781 ┆ 0.560459 ┆ 0.859948   │
│ 2011 ┆ 6254      ┆ 11002     ┆ 12663 ┆ 0.568442 ┆ 0.86883    │
│ 2012 ┆ 6237      ┆ 10863     ┆ 12693 ┆ 0.574151 ┆ 0.855826   │
│ 2013 ┆ 6458      ┆ 10878     ┆ 12533 ┆ 0.593675 ┆ 0.867949   │
│ 2014 ┆ 6493      ┆ 10830     ┆ 12658 ┆ 0.599538 ┆ 0.855585   │
│ 2015 ┆ 6487      ┆ 11009     ┆ 12895 ┆ 0.589245 ┆ 0.853742   │
│ 2016 ┆ 5884      ┆ 10670     ┆ 12350 ┆ 0.551453 ┆ 0.863968   │
│ 2017 ┆ 5575      ┆ 10589     ┆ 12201 ┆ 0.52649  ┆ 0.86788    │
│ 2018 ┆ 5637      ┆ 11021     ┆ 12567 ┆ 0.511478 ┆ 0.876979   │
│ 2019 ┆ 5372      ┆ 10861     ┆ 12256 ┆ 0.494614 ┆ 0.886178   │
│ 2020 ┆ 5199      ┆ 9997      ┆ 11279 ┆ 0.520056 ┆ 0.886337   │
│ 2021 ┆ 5197      ┆ 10528     ┆ 11748 ┆ 0.493636 ┆ 0.896153   │
│ 2022 ┆ 5334      ┆ 10881     ┆ 12062 ┆ 0.490212 ┆ 0.902089   │
│ 2023 ┆ 5142      ┆ 9745      ┆ 10717 ┆ 0.527655 ┆ 0.909303   │
│ 2024 ┆ 4478      ┆ 8842      ┆ 9540  ┆ 0.506447 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [630]:
podil_vazeb(df.filter(pl.col("stran") > 50))

shape: (25, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 2000 ┆ 4327      ┆ 8282      ┆ 10141 ┆ 0.522458 ┆ 0.816685   │
│ 2001 ┆ 4512      ┆ 8325      ┆ 10095 ┆ 0.541982 ┆ 0.824666   │
│ 2002 ┆ 4322      ┆ 8417      ┆ 10210 ┆ 0.513485 ┆ 0.824388   │
│ 2003 ┆ 4375      ┆ 8916      ┆ 10595 ┆ 0.490691 ┆ 0.841529   │
│ 2004 ┆ 4456      ┆ 9247      ┆ 10956 ┆ 0.481886 ┆ 0.844012   │
│ 2005 ┆ 4810      ┆ 9783      ┆ 11305 ┆ 0.491669 ┆ 0.865369   │
│ 2006 ┆ 4918      ┆ 10299     ┆ 11929 ┆ 0.477522 ┆ 0.863358   │
│ 2007 ┆ 5182      ┆ 10717     ┆ 12653 ┆ 0.483531 ┆ 0.846993   │
│ 2008 ┆ 5051      ┆ 11289     ┆ 13186 ┆ 0.447427 ┆ 0.856135   │
│ 2009 ┆ 4842      ┆ 10710     ┆ 12386 ┆ 0.452101 ┆ 0.864686   │
│ 2010 ┆ 4983      ┆ 10991     ┆ 12781 ┆ 0.453371 ┆ 0.859948   │
│ 2011 ┆ 5182      ┆ 11002     ┆ 12663 ┆ 0.471005 ┆ 0.86883    │
│ 2012 ┆ 5046      ┆ 10863     ┆ 12693 ┆ 0.464513 ┆ 0.855826   │
│ 2013 ┆ 5388      ┆ 10878     ┆ 12533 ┆ 0.495312 ┆ 0.867949   │
│ 2014 ┆ 5376      ┆ 10830     ┆ 12658 ┆ 0.496399 ┆ 0.855585   │
│ 2015 ┆ 5422      ┆ 11009     ┆ 12895 ┆ 0.492506 ┆ 0.853742   │
│ 2016 ┆ 4882      ┆ 10670     ┆ 12350 ┆ 0.457545 ┆ 0.863968   │
│ 2017 ┆ 4720      ┆ 10589     ┆ 12201 ┆ 0.445746 ┆ 0.86788    │
│ 2018 ┆ 4739      ┆ 11021     ┆ 12567 ┆ 0.429997 ┆ 0.876979   │
│ 2019 ┆ 4585      ┆ 10861     ┆ 12256 ┆ 0.422153 ┆ 0.886178   │
│ 2020 ┆ 4304      ┆ 9997      ┆ 11279 ┆ 0.430529 ┆ 0.886337   │
│ 2021 ┆ 4368      ┆ 10528     ┆ 11748 ┆ 0.414894 ┆ 0.896153   │
│ 2022 ┆ 4555      ┆ 10881     ┆ 12062 ┆ 0.41862  ┆ 0.902089   │
│ 2023 ┆ 4414      ┆ 9745      ┆ 10717 ┆ 0.45295  ┆ 0.909303   │
│ 2024 ┆ 3936      ┆ 8842      ┆ 9540  ┆ 0.445148 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [631]:
df.explode("655_a").group_by("655_a").len().sort(by="len",descending=True).head(100)

shape: (100, 2)
┌────────────────────────────────┬───────┐
│ 655_a                          ┆ len   │
│ ---                            ┆ ---   │
│ str                            ┆ u32   │
╞════════════════════════════════╪═══════╡
│ publikace pro děti             ┆ 29495 │
│ příručky                       ┆ 29445 │
│ handbooks and manuals          ┆ 27374 │
│ children's literature          ┆ 26870 │
│ učebnice vysokých škol         ┆ 19465 │
│ monografie                     ┆ 18691 │
│ monographs                     ┆ 17953 │
│ textbooks (higher)             ┆ 17930 │
│ populárně-naučné publikace     ┆ 14436 │
│ americké romány                ┆ 13874 │
│ American fiction               ┆ 13798 │
│ popular works                  ┆ 13745 │
│ česká poezie                   ┆ 11398 │
│ Czech poetry                   ┆ 11137 │
│ Czech fiction                  ┆ 10936 │
│ české romány                   ┆ 10908 │
│ studie                         ┆ 9791  │
│ studies                        ┆ 8683  │
│ české příběhy                  ┆ 8275  │
│ Czech stories                  ┆ 8138  │
│ fotografické publikace         ┆ 7926  │
│ essays                         ┆ 7763  │
│ English fiction                ┆ 7507  │
│ anglické romány                ┆ 7421  │
│ photographical works           ┆ 7416  │
│ detektivní romány              ┆ 6779  │
│ obrazové publikace             ┆ 6711  │
│ kolektivní monografie          ┆ 6508  │
│ collective monographs          ┆ 6447  │
│ pictorial works                ┆ 6375  │
│ detective novels               ┆ 6321  │
│ informační publikace           ┆ 6221  │
│ přehledy                       ┆ 5836  │
│ publikace pro mládež           ┆ 5759  │
│ information publications       ┆ 5536  │
│ biografie                      ┆ 5459  │
│ juvenile literature            ┆ 5388  │
│ pracovní sešity                ┆ 5347  │
│ fantasy romány                 ┆ 5333  │
│ surveys                        ┆ 5297  │
│ fantasy novels                 ┆ 5282  │
│ autobiografické vzpomínky      ┆ 5242  │
│ biography                      ┆ 5057  │
│ autobiographical reminiscences ┆ 5056  │
│ activity books                 ┆ 5024  │
│ metodické příručky             ┆ 4808  │
│ CD-ROM                         ┆ 4733  │
│ kuchařské recepty              ┆ 4512  │
│ cookbooks                      ┆ 4384  │
│ methodological manuals         ┆ 4362  │
│ leporela                       ┆ 4245  │
│ příběhy                        ┆ 4106  │
│ folding picture-books          ┆ 3996  │
│ české povídky                  ┆ 3968  │
│ historické romány              ┆ 3889  │
│ milostné romány                ┆ 3878  │
│ thrillery (romány)             ┆ 3818  │
│ thrillers (novels)             ┆ 3814  │
│ literatura faktu               ┆ 3730  │
│ historical novels              ┆ 3604  │
│ non-fiction                    ┆ 3572  │
│ české prózy                    ┆ 3568  │
│ Czech short stories            ┆ 3547  │
│ učebnice základních škol       ┆ 3434  │
│ stories                        ┆ 3405  │
│ Czech prose                    ┆ 3351  │
│ sborníky                       ┆ 3213  │
│ úvahy                          ┆ 3138  │
│ pojednání                      ┆ 3123  │
│ textbooks (elementary)         ┆ 3113  │
│ dobrodružné povídky            ┆ 2980  │
│ love novels                    ┆ 2946  │
│ učebnice středních škol        ┆ 2921  │
│ učební texty                   ┆ 2831  │
│ katalogy výstav                ┆ 2828  │
│ educational texts              ┆ 2774  │
│ adventure short stories        ┆ 2768  │
│ jubilejní publikace            ┆ 2739  │
│ textbooks (secondary)          ┆ 2704  │
│ vědecko-fantastické romány     ┆ 2702  │
│ milostné povídky               ┆ 2672  │
│ rozhovory                      ┆ 2659  │
│ učebnice                       ┆ 2650  │
│ exhibition catalogs            ┆ 2599  │
│ interviews                     ┆ 2503  │
│ science fiction novels         ┆ 2470  │
│ jubilee books                  ┆ 2445  │
│ průvodce                  

In [632]:
podil_vazeb(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "milostné povídky"))

shape: (25, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 2000 ┆ 242       ┆ 8282      ┆ 10141 ┆ 0.02922  ┆ 0.816685   │
│ 2001 ┆ 200       ┆ 8325      ┆ 10095 ┆ 0.024024 ┆ 0.824666   │
│ 2002 ┆ 75        ┆ 8417      ┆ 10210 ┆ 0.008911 ┆ 0.824388   │
│ 2003 ┆ 91        ┆ 8916      ┆ 10595 ┆ 0.010206 ┆ 0.841529   │
│ 2004 ┆ 101       ┆ 9247      ┆ 10956 ┆ 0.010922 ┆ 0.844012   │
│ 2005 ┆ 104       ┆ 9783      ┆ 11305 ┆ 0.010631 ┆ 0.865369   │
│ 2006 ┆ 71        ┆ 10299     ┆ 11929 ┆ 0.006894 ┆ 0.863358   │
│ 2007 ┆ 59        ┆ 10717     ┆ 12653 ┆ 0.005505 ┆ 0.846993   │
│ 2008 ┆ 102       ┆ 11289     ┆ 13186 ┆ 0.009035 ┆ 0.856135   │
│ 2009 ┆ 115       ┆ 10710     ┆ 12386 ┆ 0.010738 ┆ 0.864686   │
│ 2010 ┆ 92        ┆ 10991     ┆ 12781 ┆ 0.00837  ┆ 0.859948   │
│ 2011 ┆ 85        ┆ 11002     ┆ 12663 ┆ 0.007726 ┆ 0.86883    │
│ 2012 ┆ 48        ┆ 10863     ┆ 12693 ┆ 0.004419 ┆ 0.855826   │
│ 2013 ┆ 29        ┆ 10878     ┆ 12533 ┆ 0.002666 ┆ 0.867949   │
│ 2014 ┆ 33        ┆ 10830     ┆ 12658 ┆ 0.003047 ┆ 0.855585   │
│ 2015 ┆ 14        ┆ 11009     ┆ 12895 ┆ 0.001272 ┆ 0.853742   │
│ 2016 ┆ 17        ┆ 10670     ┆ 12350 ┆ 0.001593 ┆ 0.863968   │
│ 2017 ┆ 41        ┆ 10589     ┆ 12201 ┆ 0.003872 ┆ 0.86788    │
│ 2018 ┆ 34        ┆ 11021     ┆ 12567 ┆ 0.003085 ┆ 0.876979   │
│ 2019 ┆ 41        ┆ 10861     ┆ 12256 ┆ 0.003775 ┆ 0.886178   │
│ 2020 ┆ 15        ┆ 9997      ┆ 11279 ┆ 0.0015   ┆ 0.886337   │
│ 2021 ┆ 24        ┆ 10528     ┆ 11748 ┆ 0.00228  ┆ 0.896153   │
│ 2022 ┆ 9         ┆ 10881     ┆ 12062 ┆ 0.000827 ┆ 0.902089   │
│ 2023 ┆ 4         ┆ 9745      ┆ 10717 ┆ 0.00041  ┆ 0.909303   │
│ 2024 ┆ 6         ┆ 8842      ┆ 9540  ┆ 0.000679 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [633]:
podil_vazeb(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "pracovní sešity"))

shape: (25, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 2000 ┆ 39        ┆ 8282      ┆ 10141 ┆ 0.004709 ┆ 0.816685   │
│ 2001 ┆ 47        ┆ 8325      ┆ 10095 ┆ 0.005646 ┆ 0.824666   │
│ 2002 ┆ 45        ┆ 8417      ┆ 10210 ┆ 0.005346 ┆ 0.824388   │
│ 2003 ┆ 51        ┆ 8916      ┆ 10595 ┆ 0.00572  ┆ 0.841529   │
│ 2004 ┆ 58        ┆ 9247      ┆ 10956 ┆ 0.006272 ┆ 0.844012   │
│ 2005 ┆ 45        ┆ 9783      ┆ 11305 ┆ 0.0046   ┆ 0.865369   │
│ 2006 ┆ 63        ┆ 10299     ┆ 11929 ┆ 0.006117 ┆ 0.863358   │
│ 2007 ┆ 69        ┆ 10717     ┆ 12653 ┆ 0.006438 ┆ 0.846993   │
│ 2008 ┆ 53        ┆ 11289     ┆ 13186 ┆ 0.004695 ┆ 0.856135   │
│ 2009 ┆ 75        ┆ 10710     ┆ 12386 ┆ 0.007003 ┆ 0.864686   │
│ 2010 ┆ 114       ┆ 10991     ┆ 12781 ┆ 0.010372 ┆ 0.859948   │
│ 2011 ┆ 96        ┆ 11002     ┆ 12663 ┆ 0.008726 ┆ 0.86883    │
│ 2012 ┆ 125       ┆ 10863     ┆ 12693 ┆ 0.011507 ┆ 0.855826   │
│ 2013 ┆ 107       ┆ 10878     ┆ 12533 ┆ 0.009836 ┆ 0.867949   │
│ 2014 ┆ 115       ┆ 10830     ┆ 12658 ┆ 0.010619 ┆ 0.855585   │
│ 2015 ┆ 100       ┆ 11009     ┆ 12895 ┆ 0.009083 ┆ 0.853742   │
│ 2016 ┆ 129       ┆ 10670     ┆ 12350 ┆ 0.01209  ┆ 0.863968   │
│ 2017 ┆ 135       ┆ 10589     ┆ 12201 ┆ 0.012749 ┆ 0.86788    │
│ 2018 ┆ 124       ┆ 11021     ┆ 12567 ┆ 0.011251 ┆ 0.876979   │
│ 2019 ┆ 112       ┆ 10861     ┆ 12256 ┆ 0.010312 ┆ 0.886178   │
│ 2020 ┆ 151       ┆ 9997      ┆ 11279 ┆ 0.015105 ┆ 0.886337   │
│ 2021 ┆ 154       ┆ 10528     ┆ 11748 ┆ 0.014628 ┆ 0.896153   │
│ 2022 ┆ 130       ┆ 10881     ┆ 12062 ┆ 0.011947 ┆ 0.902089   │
│ 2023 ┆ 145       ┆ 9745      ┆ 10717 ┆ 0.014879 ┆ 0.909303   │
│ 2024 ┆ 75        ┆ 8842      ┆ 9540  ┆ 0.008482 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [634]:
podil_vazeb(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "česká poezie"))

shape: (25, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 2000 ┆ 131       ┆ 8282      ┆ 10141 ┆ 0.015817 ┆ 0.816685   │
│ 2001 ┆ 131       ┆ 8325      ┆ 10095 ┆ 0.015736 ┆ 0.824666   │
│ 2002 ┆ 133       ┆ 8417      ┆ 10210 ┆ 0.015801 ┆ 0.824388   │
│ 2003 ┆ 137       ┆ 8916      ┆ 10595 ┆ 0.015366 ┆ 0.841529   │
│ 2004 ┆ 163       ┆ 9247      ┆ 10956 ┆ 0.017627 ┆ 0.844012   │
│ 2005 ┆ 177       ┆ 9783      ┆ 11305 ┆ 0.018093 ┆ 0.865369   │
│ 2006 ┆ 197       ┆ 10299     ┆ 11929 ┆ 0.019128 ┆ 0.863358   │
│ 2007 ┆ 205       ┆ 10717     ┆ 12653 ┆ 0.019128 ┆ 0.846993   │
│ 2008 ┆ 250       ┆ 11289     ┆ 13186 ┆ 0.022145 ┆ 0.856135   │
│ 2009 ┆ 233       ┆ 10710     ┆ 12386 ┆ 0.021755 ┆ 0.864686   │
│ 2010 ┆ 253       ┆ 10991     ┆ 12781 ┆ 0.023019 ┆ 0.859948   │
│ 2011 ┆ 265       ┆ 11002     ┆ 12663 ┆ 0.024087 ┆ 0.86883    │
│ 2012 ┆ 242       ┆ 10863     ┆ 12693 ┆ 0.022277 ┆ 0.855826   │
│ 2013 ┆ 290       ┆ 10878     ┆ 12533 ┆ 0.026659 ┆ 0.867949   │
│ 2014 ┆ 315       ┆ 10830     ┆ 12658 ┆ 0.029086 ┆ 0.855585   │
│ 2015 ┆ 319       ┆ 11009     ┆ 12895 ┆ 0.028976 ┆ 0.853742   │
│ 2016 ┆ 330       ┆ 10670     ┆ 12350 ┆ 0.030928 ┆ 0.863968   │
│ 2017 ┆ 288       ┆ 10589     ┆ 12201 ┆ 0.027198 ┆ 0.86788    │
│ 2018 ┆ 268       ┆ 11021     ┆ 12567 ┆ 0.024317 ┆ 0.876979   │
│ 2019 ┆ 300       ┆ 10861     ┆ 12256 ┆ 0.027622 ┆ 0.886178   │
│ 2020 ┆ 323       ┆ 9997      ┆ 11279 ┆ 0.03231  ┆ 0.886337   │
│ 2021 ┆ 355       ┆ 10528     ┆ 11748 ┆ 0.03372  ┆ 0.896153   │
│ 2022 ┆ 284       ┆ 10881     ┆ 12062 ┆ 0.026101 ┆ 0.902089   │
│ 2023 ┆ 306       ┆ 9745      ┆ 10717 ┆ 0.031401 ┆ 0.909303   │
│ 2024 ┆ 244       ┆ 8842      ┆ 9540  ┆ 0.027596 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [635]:
romany_isbn = df_isbn.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "české romány").select(pl.col('isbn')).to_series().to_list()
len(romany_isbn)

8862

In [636]:
romanove_vazby = podil_vazeb(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "české romány"))
romanove_vazby

shape: (25, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 2000 ┆ 59        ┆ 8282      ┆ 10141 ┆ 0.007124 ┆ 0.816685   │
│ 2001 ┆ 45        ┆ 8325      ┆ 10095 ┆ 0.005405 ┆ 0.824666   │
│ 2002 ┆ 53        ┆ 8417      ┆ 10210 ┆ 0.006297 ┆ 0.824388   │
│ 2003 ┆ 38        ┆ 8916      ┆ 10595 ┆ 0.004262 ┆ 0.841529   │
│ 2004 ┆ 41        ┆ 9247      ┆ 10956 ┆ 0.004434 ┆ 0.844012   │
│ 2005 ┆ 56        ┆ 9783      ┆ 11305 ┆ 0.005724 ┆ 0.865369   │
│ 2006 ┆ 53        ┆ 10299     ┆ 11929 ┆ 0.005146 ┆ 0.863358   │
│ 2007 ┆ 48        ┆ 10717     ┆ 12653 ┆ 0.004479 ┆ 0.846993   │
│ 2008 ┆ 75        ┆ 11289     ┆ 13186 ┆ 0.006644 ┆ 0.856135   │
│ 2009 ┆ 90        ┆ 10710     ┆ 12386 ┆ 0.008403 ┆ 0.864686   │
│ 2010 ┆ 100       ┆ 10991     ┆ 12781 ┆ 0.009098 ┆ 0.859948   │
│ 2011 ┆ 100       ┆ 11002     ┆ 12663 ┆ 0.009089 ┆ 0.86883    │
│ 2012 ┆ 83        ┆ 10863     ┆ 12693 ┆ 0.007641 ┆ 0.855826   │
│ 2013 ┆ 83        ┆ 10878     ┆ 12533 ┆ 0.00763  ┆ 0.867949   │
│ 2014 ┆ 101       ┆ 10830     ┆ 12658 ┆ 0.009326 ┆ 0.855585   │
│ 2015 ┆ 100       ┆ 11009     ┆ 12895 ┆ 0.009083 ┆ 0.853742   │
│ 2016 ┆ 104       ┆ 10670     ┆ 12350 ┆ 0.009747 ┆ 0.863968   │
│ 2017 ┆ 119       ┆ 10589     ┆ 12201 ┆ 0.011238 ┆ 0.86788    │
│ 2018 ┆ 118       ┆ 11021     ┆ 12567 ┆ 0.010707 ┆ 0.876979   │
│ 2019 ┆ 141       ┆ 10861     ┆ 12256 ┆ 0.012982 ┆ 0.886178   │
│ 2020 ┆ 151       ┆ 9997      ┆ 11279 ┆ 0.015105 ┆ 0.886337   │
│ 2021 ┆ 221       ┆ 10528     ┆ 11748 ┆ 0.020992 ┆ 0.896153   │
│ 2022 ┆ 200       ┆ 10881     ┆ 12062 ┆ 0.018381 ┆ 0.902089   │
│ 2023 ┆ 184       ┆ 9745      ┆ 10717 ┆ 0.018881 ┆ 0.909303   │
│ 2024 ┆ 204       ┆ 8842      ┆ 9540  ┆ 0.023072 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [637]:
alt.Chart(alt_friendly(romanove_vazby.filter(pl.col("rok").is_between(1990,2024)))).mark_line().encode(alt.X("rok:T"), alt.Y("podíl:Q"))

alt.Chart(...)

In [638]:
bestsellerove_romanove_vazby = podil_vazeb(
    df.sort(by="rok").unique(
        subset=["100_a","245_a"]
    ).explode("655_a").filter(
        pl.col("655_a") == "české romány"
).explode("020_a").drop_nulls(
    subset=['020_a']
).with_columns(
    pl.col("020_a").map_elements(
        lambda x: x.replace('-','')
    ).alias("isbn")
).filter(
    pl.col("isbn").is_in(isbn_bestselleru)
))
bestsellerove_romanove_vazby

shape: (20, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 2002 ┆ 2         ┆ 8417      ┆ 10210 ┆ 0.000238 ┆ 0.824388   │
│ 2004 ┆ 1         ┆ 9247      ┆ 10956 ┆ 0.000108 ┆ 0.844012   │
│ 2005 ┆ 2         ┆ 9783      ┆ 11305 ┆ 0.000204 ┆ 0.865369   │
│ 2006 ┆ 3         ┆ 10299     ┆ 11929 ┆ 0.000291 ┆ 0.863358   │
│ 2008 ┆ 3         ┆ 11289     ┆ 13186 ┆ 0.000266 ┆ 0.856135   │
│ 2009 ┆ 3         ┆ 10710     ┆ 12386 ┆ 0.00028  ┆ 0.864686   │
│ 2010 ┆ 3         ┆ 10991     ┆ 12781 ┆ 0.000273 ┆ 0.859948   │
│ 2011 ┆ 1         ┆ 11002     ┆ 12663 ┆ 0.000091 ┆ 0.86883    │
│ 2012 ┆ 3         ┆ 10863     ┆ 12693 ┆ 0.000276 ┆ 0.855826   │
│ 2014 ┆ 5         ┆ 10830     ┆ 12658 ┆ 0.000462 ┆ 0.855585   │
│ 2015 ┆ 1         ┆ 11009     ┆ 12895 ┆ 0.000091 ┆ 0.853742   │
│ 2016 ┆ 3         ┆ 10670     ┆ 12350 ┆ 0.000281 ┆ 0.863968   │
│ 2017 ┆ 4         ┆ 10589     ┆ 12201 ┆ 0.000378 ┆ 0.86788    │
│ 2018 ┆ 4         ┆ 11021     ┆ 12567 ┆ 0.000363 ┆ 0.876979   │
│ 2019 ┆ 1         ┆ 10861     ┆ 12256 ┆ 0.000092 ┆ 0.886178   │
│ 2020 ┆ 1         ┆ 9997      ┆ 11279 ┆ 0.0001   ┆ 0.886337   │
│ 2021 ┆ 3         ┆ 10528     ┆ 11748 ┆ 0.000285 ┆ 0.896153   │
│ 2022 ┆ 1         ┆ 10881     ┆ 12062 ┆ 0.000092 ┆ 0.902089   │
│ 2023 ┆ 7         ┆ 9745      ┆ 10717 ┆ 0.000718 ┆ 0.909303   │
│ 2024 ┆ 2         ┆ 8842      ┆ 9540  ┆ 0.000226 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [639]:
alt.Chart(alt_friendly(bestsellerove_romanove_vazby.filter(pl.col("rok").is_between(1990,2024)))).mark_line().encode(alt.X("rok:T"), alt.Y("podíl:Q"))

alt.Chart(...)

In [640]:
bestsellery = pd.read_json(os.path.join("data","sckn_zebricky.json"))
bestsellery = pl.from_pandas(bestsellery)
bestsellery
isbn_bestselleru = set(bestsellery.select(pl.col("sckn_isbn")).to_series().to_list())
df_isbn = df.explode("020_a").drop_nulls(subset=['020_a']).with_columns(pl.col("020_a").map_elements(lambda x: x.replace('-','')).alias("isbn"))

In [641]:
df_isbn.filter(pl.col('isbn').is_in(isbn_bestselleru))

shape: (6_310, 76)
┌──────────┬────────────────────────┬────────────────┬────────────────┬───┬───────┬───────────┬───────┬───────────────┐
│ 100_ind1 ┆ 100_a                  ┆ 100_7          ┆ 100_4          ┆ … ┆ stran ┆ vazba     ┆ vyska ┆ isbn          │
│ ---      ┆ ---                    ┆ ---            ┆ ---            ┆   ┆ ---   ┆ ---       ┆ ---   ┆ ---           │
│ str      ┆ str                    ┆ str            ┆ list[str]      ┆   ┆ i64   ┆ str       ┆ i64   ┆ str           │
╞══════════╪════════════════════════╪════════════════╪════════════════╪═══╪═══════╪═══════════╪═══════╪═══════════════╡
│ 1        ┆ Špidlík, Tomáš,        ┆ jn19990218115  ┆ ["aut"]        ┆ … ┆ 82    ┆ pevná     ┆ 22    ┆ 9788074120589 │
│ 1        ┆ Francis, Felix,        ┆ xx0078475      ┆ ["aut"]        ┆ … ┆ 287   ┆ pevná     ┆ 24    ┆ 9788024264103 │
│ 1        ┆ Lane, Leena            ┆ mzk2008469189  ┆ ["aut"]        ┆ … ┆ 191   ┆ brožovaná ┆ 19    ┆ 9788071954637 │
│ 1        ┆ Drijverová, Martina,   ┆ jk01023067     ┆ ["aut"]        ┆ … ┆ 62    ┆ pevná     ┆ 21    ┆ 9788000026268 │
│ 1        ┆ Vaněk, Roman,          ┆ xx0110388      ┆ ["aut"]        ┆ … ┆ 622   ┆ pevná     ┆ 28    ┆ 9788087737279 │
│ 1        ┆ Ferrante, Elena,       ┆ pag2008454838  ┆ ["aut"]        ┆ … ┆ 423   ┆ brožovaná ┆ 20    ┆ 9788072603763 │
│ 1        ┆ Maas, Sarah J.,        ┆ xx0197098      ┆ ["aut"]        ┆ … ┆ 820   ┆ pevná     ┆ 21    ┆ 9788074987366 │
│ 1        ┆ Gawliczková, Dominika, ┆ ola2018997056  ┆ ["aut"]        ┆ … ┆ 326   ┆ pevná     ┆ 22    ┆ 9788026418542 │
│ 1        ┆ Chancellor, Deborah,   ┆ mzk2003202409  ┆ ["aut"]        ┆ … ┆ 48    ┆ pevná     ┆ 32    ┆ 9788025318850 │
│ 1        ┆ Hausmann, Josef,       ┆ jn19990010067  ┆ ["aut"]        ┆ … ┆ 131   ┆ brožovaná ┆ 21    ┆ 9788086563251 │
│ 1        ┆ Davídková, Tereza      ┆ jo2015853995   ┆ ["aut"]        ┆ … ┆ 93    ┆ pevná     ┆ 23    ┆ 9788072438044 │
│ 1        ┆ Kent, Rina             ┆ osa20231198221 ┆ ["aut"]        ┆ … ┆ 299   ┆ brožovaná ┆ 20    ┆ 9788027723720 │
│ 1        ┆ Armstrong, Lance,      ┆ xx0002538      ┆ ["aut"]        ┆ … ┆ 237   ┆ pevná     ┆ 21    ┆ 8072542575    │
│ 1        ┆ Brabenec, Vratislav,   ┆ jn20010309458  ┆ ["aut"]        ┆ … ┆ 38    ┆ pevná     ┆ 20    ┆ 9788087596654 │
│ 1        ┆ Bečková, Kateřina,     ┆ jn20001227077  ┆ ["aut"]        ┆ … ┆ 143   ┆ null      ┆ 21    ┆ 8071856088    │
│ 1        ┆ Fleischmannová, Emílie ┆ jn20010309247  ┆ ["aut"]        ┆ … ┆ 119   ┆ null      ┆ 30    ┆ 807168919X    │
│ 1        ┆ Šandera, Jiří,         ┆ mzk2003211118  ┆ ["aut"]        ┆ … ┆ 56    ┆ pevná     ┆ 30    ┆ 9788025318799 │
│ 1        ┆ Pawlowská, Halina,     ┆ jn99240000851  ┆ ["aut"]        ┆ … ┆ 349   ┆ pevná     ┆ 19    ┆ 9788026725947 │
│ 1        ┆ Blyton, Enid,          ┆ jn19990000860  ┆ ["aut"]        ┆ … ┆ 128   ┆ pevná     ┆ 21    ┆ 8000012405    │
│ 1        ┆ Soukupová, Petra,      ┆ xx0067507      ┆ ["aut"]        ┆ … ┆ 207   ┆ pevná     ┆ 24    ┆ 9788027501298 │
│ 1        ┆ Bruckner, Vanda,       ┆ xx0308776      ┆ ["aut"]        ┆ … ┆ 126   ┆ pevná     ┆ 21    ┆ 9788027723874 │
│ 1        ┆ Belmondo, Jean-Paul,   ┆ jn20000700148  ┆ ["aut"]        ┆ … ┆ 247   ┆ pevná     ┆ 22    ┆ 9788072527076 │
│ 1        ┆ Torčík, Marek,         ┆ xx0209774      ┆ ["aut"]        ┆ … ┆ 266   ┆ brožovaná ┆ 20    ┆ 9788076373990 │
│ 1        ┆ Mayle, Peter,          ┆ xx0004471      ┆ ["aut"]        ┆ … ┆ 127   ┆ pevná     ┆ 21    ┆ 9788025714713 │
│ 1        ┆ Šimotová, Adriena,     ┆ jn19990209857  ┆ ["aut", "ill"] ┆ … ┆ 41    ┆ pevná     ┆ 27    ┆ 9788027007080 │
│ 1        ┆ Horecký, Michal        ┆ null           ┆ ["aut"]        ┆ … ┆ 97    ┆ pevná     ┆ 22    ┆ 8086132641    │
│ 1        ┆ Francis, Felix,        ┆ xx0078475      ┆ ["aut"]        ┆ … ┆ 292   ┆ pevná     ┆ 24    ┆ 9788024244358 │
│ 1        ┆ Burton, Tim,           ┆ js20050822016  ┆ ["aut"]        ┆ … ┆ 120   ┆ pevná     ┆ 18    ┆ 9788074381003 │
│ 1        ┆ Borovičk

In [642]:
alt.Chart(alt_friendly(romanove_vazby.filter(pl.col("rok").is_between(1990,2024)))).mark_line().encode(alt.X("rok:T"), alt.Y("podíl:Q"))

alt.Chart(...)

## Rozmery

In [644]:
rozsah = df.filter(~pl.col("stran").is_null()).group_by("rok").len().sort(by="rok").rename({"len":"vyplněno"})
rozsah = rozsah.join(df.group_by("rok").len().sort(by="rok").rename({"len":"vše"}), left_on="rok", right_on="rok", how="left")
rozsah = rozsah.with_columns((pl.col("vyplněno") / pl.col("vše")).alias("vyplněnost"))
rozsah

shape: (25, 4)
┌──────┬──────────┬───────┬────────────┐
│ rok  ┆ vyplněno ┆ vše   ┆ vyplněnost │
│ ---  ┆ ---      ┆ ---   ┆ ---        │
│ i64  ┆ u32      ┆ u32   ┆ f64        │
╞══════╪══════════╪═══════╪════════════╡
│ 2000 ┆ 10137    ┆ 10141 ┆ 0.999606   │
│ 2001 ┆ 10092    ┆ 10095 ┆ 0.999703   │
│ 2002 ┆ 10203    ┆ 10210 ┆ 0.999314   │
│ 2003 ┆ 10588    ┆ 10595 ┆ 0.999339   │
│ 2004 ┆ 10947    ┆ 10956 ┆ 0.999179   │
│ 2005 ┆ 11298    ┆ 11305 ┆ 0.999381   │
│ 2006 ┆ 11925    ┆ 11929 ┆ 0.999665   │
│ 2007 ┆ 12646    ┆ 12653 ┆ 0.999447   │
│ 2008 ┆ 13186    ┆ 13186 ┆ 1.0        │
│ 2009 ┆ 12384    ┆ 12386 ┆ 0.999839   │
│ 2010 ┆ 12781    ┆ 12781 ┆ 1.0        │
│ 2011 ┆ 12663    ┆ 12663 ┆ 1.0        │
│ 2012 ┆ 12693    ┆ 12693 ┆ 1.0        │
│ 2013 ┆ 12533    ┆ 12533 ┆ 1.0        │
│ 2014 ┆ 12658    ┆ 12658 ┆ 1.0        │
│ 2015 ┆ 12895    ┆ 12895 ┆ 1.0        │
│ 2016 ┆ 12350    ┆ 12350 ┆ 1.0        │
│ 2017 ┆ 12201    ┆ 12201 ┆ 1.0        │
│ 2018 ┆ 12567    ┆ 12567 ┆ 1.0        │
│ 2019 ┆ 12256    ┆ 12256 ┆ 1.0        │
│ 2020 ┆ 11279    ┆ 11279 ┆ 1.0        │
│ 2021 ┆ 11748    ┆ 11748 ┆ 1.0        │
│ 2022 ┆ 12062    ┆ 12062 ┆ 1.0        │
│ 2023 ┆ 10716    ┆ 10717 ┆ 0.999907   │
│ 2024 ┆ 9540     ┆ 9540  ┆ 1.0        │
└──────┴──────────┴───────┴────────────┘

In [645]:
def streni_tloustka(frejm):
    return frejm.group_by("rok").agg(pl.col("stran").median()).sort(by="rok").with_columns(
                   pl.col("rok").map_elements(
                       lambda x: datetime.date(year=int(x), month=1, day=1), 
                       return_dtype=pl.Date
                   ).cast(pl.Datetime))

In [646]:
tloustky_romanu = df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "české romány").filter(pl.col("rok") >= 1990)

In [647]:
tloustky_romanu.select(pl.col("stran"))

shape: (8_893, 1)
┌───────┐
│ stran │
│ ---   │
│ i64   │
╞═══════╡
│ 459   │
│ 383   │
│ 127   │
│ 315   │
│ 182   │
│ 313   │
│ 338   │
│ 158   │
│ 207   │
│ 496   │
│ 399   │
│ 356   │
│ 373   │
│ 231   │
│ 195   │
│ 213   │
│ 239   │
│ 207   │
│ 261   │
│ 220   │
│ 205   │
│ 181   │
│ 181   │
│ 205   │
│ 133   │
│ 361   │
│ 412   │
│ 3     │
│ 127   │
│ 414   │
│ 190   │
│ 99    │
│ 399   │
│ 246   │
│ 176   │
│ 135   │
│ 255   │
│ 192   │
│ 243   │
│ 197   │
│ 205   │
│ 261   │
│ 186   │
│ 131   │
│ 265   │
│ 325   │
│ 185   │
│ 220   │
│ 234   │
│ 511   │
│ …     │
│ 269   │
│ 181   │
│ 240   │
│ 173   │
│ 333   │
│ 341   │
│ 187   │
│ 255   │
│ 324   │
│ 190   │
│ 637   │
│ 179   │
│ 179   │
│ 315   │
│ 413   │
│ 403   │
│ 259   │
│ 191   │
│ 227   │
│ 213   │
│ 269   │
│ 158   │
│ 247   │
│ 277   │
│ 119   │
│ 333   │
│ 271   │
│ 335   │
│ 350   │
│ 256   │
│ 271   │
│ 507   │
│ 493   │
│ 475   │
│ 278   │
│ 349   │
│ 276   │
│ 365   │
│ 158   │
│ 321   │
│ 300   │
│ 207   │
│ 229   │
│ 311   │
│ 149   │
│ 169   │
│ 237   │
│ 230   │
│ 204   │
│ 187   │
└───────┘

In [648]:
tloustky_romanu.sort(by='stran',descending=True).select(pl.col(["rok","100_a","245_a","stran"]))

shape: (8_893, 4)
┌──────┬─────────────────────────┬─────────────────────────────────┬───────┐
│ rok  ┆ 100_a                   ┆ 245_a                           ┆ stran │
│ ---  ┆ ---                     ┆ ---                             ┆ ---   │
│ i64  ┆ str                     ┆ str                             ┆ i64   │
╞══════╪═════════════════════════╪═════════════════════════════════╪═══════╡
│ 2021 ┆ Motýl, Petr,            ┆ Šatna a klášter                 ┆ 1193  │
│ 2005 ┆ Slanská, Mariana        ┆ Tóny v trní                     ┆ 1101  │
│ 2014 ┆ Novotný, František,     ┆ Valhala                         ┆ 1086  │
│ 2024 ┆ BasthArt,               ┆ Bastard                         ┆ 1085  │
│ 2024 ┆ Beneš, Filip,           ┆ Černý měsíc                     ┆ 1000  │
│ 2013 ┆ Sabina, Karel,          ┆ Král Ferdinand V. Dobrotivý a … ┆ 951   │
│ 2019 ┆ Hyrsch, Áron,           ┆ Hora rabínova                   ┆ 929   │
│ 2023 ┆ Šalda, Ladislav,        ┆ Ta hra neměla pravidla          ┆ 868   │
│ 2006 ┆ Stránský, Jiří,         ┆ Zdivočelá země                  ┆ 867   │
│ 2002 ┆ Erben, Václav,          ┆ Paměti českého krále Jiříka z … ┆ 862   │
│ 2020 ┆ Kučera, Dalibor,        ┆ Poté                            ┆ 836   │
│ 2015 ┆ Durych, Jaroslav,       ┆ Bloudění                        ┆ 832   │
│ 2018 ┆ Dobeš, Jára,            ┆ Stigmata karmy                  ┆ 816   │
│ 2017 ┆ Svobodová, Jitka        ┆ Přemyslova krev                 ┆ 812   │
│ 2001 ┆ Neff, Ondřej,           ┆ Milénium                        ┆ 799   │
│ 2002 ┆ Schulz, Karel,          ┆ Kámen a bolest                  ┆ 796   │
│ 2021 ┆ Levithann, Revy,        ┆ Vrah z Bellevillu               ┆ 796   │
│ 2010 ┆ Fiala, Dominik,         ┆ Láska až za hrob                ┆ 786   │
│ 2019 ┆ Vondruška, Vlastimil,   ┆ Kronika zániku Evropy           ┆ 779   │
│ 2004 ┆ Novák, Jan,             ┆ Zatím dobrý                     ┆ 776   │
│ 2007 ┆ Filip, Ota,             ┆ Osmý, čili, Nedokončený životo… ┆ 773   │
│ 2022 ┆ Lipner, Tomáš,          ┆ Hvězdolet Vltava                ┆ 765   │
│ 2021 ┆ Horák, Ondřej,          ┆ Pohlavní styky                  ┆ 759   │
│ 2021 ┆ Hamouz, Jan,            ┆ Třetí ucho                      ┆ 756   │
│ 2019 ┆ Štolba, Jan,            ┆ Nezastavitelný den              ┆ 756   │
│ 2011 ┆ Kučera, Dalibor,        ┆ Dům soumraku                    ┆ 752   │
│ 2024 ┆ Krejčík, Přemysl,       ┆ Rochus                          ┆ 751   │
│ 2006 ┆ Fuks, Ladislav,         ┆ Vévodkyně a kuchařka            ┆ 749   │
│ 2018 ┆ Denemarková, Radka,     ┆ Hodiny z olova                  ┆ 747   │
│ 2019 ┆ Bareš, Pavel,           ┆ Kronovy děti                    ┆ 746   │
│ 2016 ┆ Vaňková, Ludmila,       ┆ Karel IV.                       ┆ 743   │
│ 2017 ┆ Šlejhar, Josef Karel,   ┆ Cvrček mého krbu                ┆ 739   │
│ 2022 ┆ Velinský, Jaroslav,     ┆ Případy Augustina Velikého & s… ┆ 738   │
│ 2024 ┆ Haidingerová, Kristina, ┆ Očistec                         ┆ 734   │
│ 2019 ┆ Ajvaz, Michal,          ┆ Města                           ┆ 724   │
│ 2022 ┆ Cima, Anna,             ┆ Vzpomínky na úhoře              ┆ 718   │
│ 2014 ┆ Kahuda, Václav,         ┆ Vítr, tma, přítomnost           ┆ 715   │
│ 2023 ┆ Ruščáková, Dagmar       ┆ Alžběta a drak                  ┆ 710   │
│ 2023 ┆ Petrásek, Tomáš,        ┆ Azhareida                       ┆ 705   │
│ 2008 ┆ Mlynkec, Tomáš,         ┆ Slavíci kamenného mostu         ┆ 704   │
│ 2024 ┆ Škabraha, Martin,       ┆ Kníže Moravanů                  ┆ 692   │
│ 2014 ┆ Hlávka, Jan,            ┆ Tenký led                       ┆ 690   │
│ 2024 ┆ Nightshade, Ella,       ┆ Gorme                           ┆ 686   │
│ 2017 ┆ Cerman, Petr            ┆ Bureš                           ┆ 686   │
│ 2022 ┆ Tučková, Kateřina,      ┆ Bílá Voda                       ┆ 686   │
│ 2003 ┆ Niedl, František,       ┆ Vzpomínky jednoho lumpa         ┆ 685   │
│ 2001 ┆ Matoušek, Ivan,         ┆ Spas                

In [649]:
do_grafu = tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").quantile(0.25).alias('malo')).join(
    tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").quantile(0.75).alias('hodne')), on="rok"
).join(
    tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").median().alias('median')), on="rok"
).join(
    tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").min().alias('min')), on="rok"
).join(
    tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").max().alias('max')), on="rok"
)
do_grafu

shape: (25, 6)
┌──────┬───────┬───────┬────────┬─────┬──────┐
│ rok  ┆ malo  ┆ hodne ┆ median ┆ min ┆ max  │
│ ---  ┆ ---   ┆ ---   ┆ ---    ┆ --- ┆ ---  │
│ i64  ┆ f64   ┆ f64   ┆ f64    ┆ i64 ┆ i64  │
╞══════╪═══════╪═══════╪════════╪═════╪══════╡
│ 2017 ┆ 206.0 ┆ 322.0 ┆ 254.0  ┆ 96  ┆ 812  │
│ 2013 ┆ 195.0 ┆ 285.0 ┆ 237.0  ┆ 79  ┆ 951  │
│ 2021 ┆ 211.0 ┆ 335.0 ┆ 267.5  ┆ 62  ┆ 1193 │
│ 2015 ┆ 210.0 ┆ 320.0 ┆ 255.0  ┆ 82  ┆ 832  │
│ 2022 ┆ 214.0 ┆ 340.0 ┆ 275.0  ┆ 91  ┆ 765  │
│ 2002 ┆ 158.0 ┆ 291.0 ┆ 219.5  ┆ 85  ┆ 862  │
│ 2019 ┆ 209.0 ┆ 341.0 ┆ 261.0  ┆ 94  ┆ 929  │
│ 2011 ┆ 181.0 ┆ 293.0 ┆ 226.0  ┆ 84  ┆ 752  │
│ 2009 ┆ 162.0 ┆ 290.0 ┆ 226.0  ┆ 52  ┆ 634  │
│ 2001 ┆ 143.0 ┆ 272.0 ┆ 197.0  ┆ 92  ┆ 799  │
│ 2018 ┆ 213.0 ┆ 320.0 ┆ 253.5  ┆ 44  ┆ 816  │
│ 2023 ┆ 218.0 ┆ 344.0 ┆ 273.5  ┆ 49  ┆ 868  │
│ 2007 ┆ 171.0 ┆ 288.0 ┆ 222.0  ┆ 99  ┆ 773  │
│ 2008 ┆ 166.0 ┆ 290.0 ┆ 222.0  ┆ 83  ┆ 704  │
│ 2003 ┆ 157.0 ┆ 286.0 ┆ 220.0  ┆ 91  ┆ 685  │
│ 2020 ┆ 211.0 ┆ 321.0 ┆ 259.0  ┆ 99  ┆ 836  │
│ 2014 ┆ 208.0 ┆ 316.0 ┆ 248.0  ┆ 64  ┆ 1086 │
│ 2012 ┆ 185.0 ┆ 310.0 ┆ 234.0  ┆ 58  ┆ 645  │
│ 2006 ┆ 165.0 ┆ 291.0 ┆ 223.0  ┆ 102 ┆ 867  │
│ 2004 ┆ 151.0 ┆ 289.0 ┆ 216.0  ┆ 82  ┆ 776  │
│ 2005 ┆ 165.0 ┆ 275.0 ┆ 215.0  ┆ 61  ┆ 1101 │
│ 2010 ┆ 190.0 ┆ 294.0 ┆ 229.0  ┆ 91  ┆ 786  │
│ 2016 ┆ 207.0 ┆ 320.0 ┆ 257.0  ┆ 39  ┆ 743  │
│ 2000 ┆ 149.0 ┆ 269.0 ┆ 202.0  ┆ 70  ┆ 637  │
│ 2024 ┆ 222.0 ┆ 349.0 ┆ 282.5  ┆ 82  ┆ 1085 │
└──────┴───────┴───────┴────────┴─────┴──────┘

In [650]:
tloustky_romanu = tloustky_romanu.join(do_grafu, on="rok")

In [651]:
nejtlustsi = tloustky_romanu.sort(by="stran",descending=True).filter(pl.col("stran") > 600)
nejtlustsi

shape: (96, 80)
┌──────────┬───────────────────────────┬───────────────────┬────────────────┬───┬───────┬────────┬─────┬──────┐
│ 100_ind1 ┆ 100_a                     ┆ 100_7             ┆ 100_4          ┆ … ┆ hodne ┆ median ┆ min ┆ max  │
│ ---      ┆ ---                       ┆ ---               ┆ ---            ┆   ┆ ---   ┆ ---    ┆ --- ┆ ---  │
│ str      ┆ str                       ┆ str               ┆ list[str]      ┆   ┆ f64   ┆ f64    ┆ i64 ┆ i64  │
╞══════════╪═══════════════════════════╪═══════════════════╪════════════════╪═══╪═══════╪════════╪═════╪══════╡
│ 1        ┆ Motýl, Petr,              ┆ jn99240000739     ┆ ["aut"]        ┆ … ┆ 335.0 ┆ 267.5  ┆ 62  ┆ 1193 │
│ 1        ┆ Slanská, Mariana          ┆ xx0039997         ┆ ["aut"]        ┆ … ┆ 275.0 ┆ 215.0  ┆ 61  ┆ 1101 │
│ 1        ┆ Novotný, František,       ┆ jo2002106771      ┆ ["aut"]        ┆ … ┆ 316.0 ┆ 248.0  ┆ 64  ┆ 1086 │
│ 0        ┆ BasthArt,                 ┆ xx0318468         ┆ ["aut"]        ┆ … ┆ 349.0 ┆ 282.5  ┆ 82  ┆ 1085 │
│ 1        ┆ Beneš, Filip,             ┆ hka20251248754    ┆ ["aut"]        ┆ … ┆ 349.0 ┆ 282.5  ┆ 82  ┆ 1085 │
│ 1        ┆ Sabina, Karel,            ┆ jk01110239        ┆ ["aut"]        ┆ … ┆ 285.0 ┆ 237.0  ┆ 79  ┆ 951  │
│ 1        ┆ Hyrsch, Áron,             ┆ xx0201017         ┆ ["aut", "ill"] ┆ … ┆ 341.0 ┆ 261.0  ┆ 94  ┆ 929  │
│ 1        ┆ Šalda, Ladislav,          ┆ ola2011650927     ┆ ["aut"]        ┆ … ┆ 344.0 ┆ 273.5  ┆ 49  ┆ 868  │
│ 1        ┆ Stránský, Jiří,           ┆ jk01121359        ┆ ["aut"]        ┆ … ┆ 291.0 ┆ 223.0  ┆ 102 ┆ 867  │
│ 1        ┆ Erben, Václav,            ┆ jk01030537        ┆ ["aut"]        ┆ … ┆ 291.0 ┆ 219.5  ┆ 85  ┆ 862  │
│ 1        ┆ Kučera, Dalibor,          ┆ jo2013793651      ┆ ["aut"]        ┆ … ┆ 321.0 ┆ 259.0  ┆ 99  ┆ 836  │
│ 1        ┆ Durych, Jaroslav,         ┆ jk01023358        ┆ ["aut"]        ┆ … ┆ 320.0 ┆ 255.0  ┆ 82  ┆ 832  │
│ 1        ┆ Dobeš, Jára,              ┆ jo2002143940      ┆ ["aut"]        ┆ … ┆ 320.0 ┆ 253.5  ┆ 44  ┆ 816  │
│ 1        ┆ Svobodová, Jitka          ┆ jo2017966018      ┆ ["aut"]        ┆ … ┆ 322.0 ┆ 254.0  ┆ 96  ┆ 812  │
│ 1        ┆ Neff, Ondřej,             ┆ jk01082907        ┆ ["aut"]        ┆ … ┆ 272.0 ┆ 197.0  ┆ 92  ┆ 799  │
│ 1        ┆ Schulz, Karel,            ┆ jk01111165        ┆ ["aut"]        ┆ … ┆ 291.0 ┆ 219.5  ┆ 85  ┆ 862  │
│ 1        ┆ Levithann, Revy,          ┆ jo20211118644     ┆ ["aut"]        ┆ … ┆ 335.0 ┆ 267.5  ┆ 62  ┆ 1193 │
│ 1        ┆ Fiala, Dominik,           ┆ jx20100720021     ┆ ["aut"]        ┆ … ┆ 294.0 ┆ 229.0  ┆ 91  ┆ 786  │
│ 1        ┆ Vondruška, Vlastimil,     ┆ xx0004129         ┆ ["aut"]        ┆ … ┆ 341.0 ┆ 261.0  ┆ 94  ┆ 929  │
│ 1        ┆ Novák, Jan,               ┆ jn19990209593     ┆ ["aut"]        ┆ … ┆ 289.0 ┆ 216.0  ┆ 82  ┆ 776  │
│ 1        ┆ Filip, Ota,               ┆ jk01031164        ┆ ["aut"]        ┆ … ┆ 288.0 ┆ 222.0  ┆ 99  ┆ 773  │
│ 1        ┆ Lipner, Tomáš,            ┆ mub2011655109     ┆ ["aut"]        ┆ … ┆ 340.0 ┆ 275.0  ┆ 91  ┆ 765  │
│ 1        ┆ Horák, Ondřej,            ┆ js20020122074     ┆ ["aut"]        ┆ … ┆ 335.0 ┆ 267.5  ┆ 62  ┆ 1193 │
│ 1        ┆ Hamouz, Jan,              ┆ xx0228008         ┆ ["aut"]        ┆ … ┆ 335.0 ┆ 267.5  ┆ 62  ┆ 1193 │
│ 1        ┆ Štolba, Jan,              ┆ jn19990218117     ┆ ["aut"]        ┆ … ┆ 341.0 ┆ 261.0  ┆ 94  ┆ 929  │
│ 1        ┆ Kučera, Dalibor,          ┆ jo2013793651      ┆ ["aut"]        ┆ … ┆ 293.0 ┆ 226.0  ┆ 84  ┆ 752  │
│ 1        ┆ Krejčík, Přemysl,         ┆ xx0197400         ┆ ["aut"]        ┆ … ┆ 349.0 ┆ 282.5  ┆ 82  ┆ 1085 │
│ 1        ┆ Fuks, Ladislav,           ┆ jk01032159        ┆ ["aut"]        ┆ … ┆ 291.0 ┆ 223.0  ┆ 102 ┆ 867  │
│ 1        ┆ Denemarková, Radka,       ┆ xx0002871         ┆ ["aut"]        ┆ … ┆ 320.0 ┆ 253.5  ┆ 44  ┆ 816  │
│ 1        ┆ Bareš, Pavel,             ┆ xx0213244         ┆ ["aut"]        ┆ … ┆ 341.0 ┆ 261.0  ┆ 94  ┆ 929  │
│ 1        ┆ Vaňková, Ludmila,         ┆ jk01141586        ┆ ["a

In [652]:
streni_tloustka(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "české romány"))

shape: (25, 2)
┌─────────────────────┬───────┐
│ rok                 ┆ stran │
│ ---                 ┆ ---   │
│ datetime[μs]        ┆ f64   │
╞═════════════════════╪═══════╡
│ 2000-01-01 00:00:00 ┆ 202.0 │
│ 2001-01-01 00:00:00 ┆ 197.0 │
│ 2002-01-01 00:00:00 ┆ 219.0 │
│ 2003-01-01 00:00:00 ┆ 220.0 │
│ 2004-01-01 00:00:00 ┆ 215.0 │
│ 2005-01-01 00:00:00 ┆ 215.0 │
│ 2006-01-01 00:00:00 ┆ 223.0 │
│ 2007-01-01 00:00:00 ┆ 222.0 │
│ 2008-01-01 00:00:00 ┆ 222.0 │
│ 2009-01-01 00:00:00 ┆ 226.0 │
│ 2010-01-01 00:00:00 ┆ 229.0 │
│ 2011-01-01 00:00:00 ┆ 225.0 │
│ 2012-01-01 00:00:00 ┆ 231.0 │
│ 2013-01-01 00:00:00 ┆ 231.0 │
│ 2014-01-01 00:00:00 ┆ 247.0 │
│ 2015-01-01 00:00:00 ┆ 255.0 │
│ 2016-01-01 00:00:00 ┆ 255.5 │
│ 2017-01-01 00:00:00 ┆ 253.0 │
│ 2018-01-01 00:00:00 ┆ 253.0 │
│ 2019-01-01 00:00:00 ┆ 261.0 │
│ 2020-01-01 00:00:00 ┆ 258.5 │
│ 2021-01-01 00:00:00 ┆ 267.0 │
│ 2022-01-01 00:00:00 ┆ 271.0 │
│ 2023-01-01 00:00:00 ┆ 272.0 │
│ 2024-01-01 00:00:00 ┆ 282.0 │
└─────────────────────┴───────┘

In [789]:
rozptyl = alt.Chart(alt_friendly(do_grafu), title=alt.Title("Český román bobtná", subtitle=["Střední délka románu narostla od roku 2000 o 80 stran.","Výška naprosté většiny výtisků zůstává 21 centimetrů."]), 
                    width=300).mark_area(opacity=0.5, color='#445B78').encode(
       alt.X("rok:T", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')).title(None),
    alt.Y("hodne:Q", axis=alt.Axis(domainOpacity=0, format='d', tickColor='#DCDDD6')).title(None),
    alt.Y2("malo:Q")
)

median = alt.Chart(alt_friendly(do_grafu), width=300).mark_line(color='#445B78').encode(
       alt.X("rok:T", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
    alt.Y("median:Q", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6'), scale=alt.Scale(domain=[0,400]))
)

#kraje = alt.Chart(alt_friendly(tloustky_romanu.filter(pl.col("stran") > 30).filter(~pl.col('stran').is_between(pl.col('malo'),pl.col('hodne')))), width=300).mark_point(size=1, opacity=0.1).encode(
#       alt.X("rok:T", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
#    alt.Y("max:Q", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')))

finale =  alt.layer(
#    kraje,
    rozptyl,
    median
).configure_view(stroke='transparent').resolve_scale(color="independent")

finale

alt.LayerChart(...)

In [654]:
vysky_romanu = df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "české romány").filter(pl.col("rok") >= 1990)

In [655]:
do_grafu_vyska = vysky_romanu.group_by("rok").agg(pl.col('vyska').median().alias('střední výška')).join(
    vysky_romanu.group_by("rok").agg(pl.col("vyska").quantile(0.95).alias('hodne')), on="rok"
).join(
    vysky_romanu.group_by("rok").agg(pl.col("vyska").quantile(0.05).alias('malo')), on="rok"
)
do_grafu_vyska.sort(by="rok")

shape: (25, 4)
┌──────┬───────────────┬───────┬──────┐
│ rok  ┆ střední výška ┆ hodne ┆ malo │
│ ---  ┆ ---           ┆ ---   ┆ ---  │
│ i64  ┆ f64           ┆ f64   ┆ f64  │
╞══════╪═══════════════╪═══════╪══════╡
│ 2000 ┆ 21.0          ┆ 22.0  ┆ 18.0 │
│ 2001 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2002 ┆ 21.0          ┆ 22.0  ┆ 18.0 │
│ 2003 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2004 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2005 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2006 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2007 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2008 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2009 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2010 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2011 ┆ 21.0          ┆ 23.0  ┆ 17.0 │
│ 2012 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2013 ┆ 21.0          ┆ 22.0  ┆ 17.0 │
│ 2014 ┆ 21.0          ┆ 24.0  ┆ 18.0 │
│ 2015 ┆ 21.0          ┆ 22.0  ┆ 18.0 │
│ 2016 ┆ 21.0          ┆ 22.0  ┆ 18.0 │
│ 2017 ┆ 21.0          ┆ 22.0  ┆ 18.0 │
│ 2018 ┆ 21.0          ┆ 23.0  ┆ 18.0 │
│ 2019 ┆ 21.0          ┆ 22.0  ┆ 18.0 │
│ 2020 ┆ 21.0          ┆ 22.0  ┆ 18.0 │
│ 2021 ┆ 21.0          ┆ 22.0  ┆ 19.0 │
│ 2022 ┆ 21.0          ┆ 22.0  ┆ 19.0 │
│ 2023 ┆ 21.0          ┆ 22.0  ┆ 19.0 │
│ 2024 ┆ 21.0          ┆ 22.0  ┆ 19.0 │
└──────┴───────────────┴───────┴──────┘

## Vs. hodnocení

In [731]:
gr = pd.read_csv(os.path.join('data','goodreads-hodnoceni-extra.csv'))
gr = pl.from_pandas(gr)
gr = gr.sort(by="GR_date").unique(subset=['GR_isbn'],keep='last')
dk = pd.read_csv(os.path.join('data','databazeknih-hodnoceni-extra.csv'))
dk = pl.from_pandas(dk).with_columns(pl.col("DK_isbn").map_elements(lambda x: x.replace(".0","")))
dk = dk.sort(by="DK_date").unique(subset=['DK_isbn'],keep='last')

In [733]:
gr

shape: (3_136, 14)
┌───────────────┬────────────┬────────────────────────┬───────────┬───┬────────────┬────────────┬──────────┬───────────┐
│ GR_isbn       ┆ GR_date    ┆ GR_title               ┆ GR_rating ┆ … ┆ GR_4_stars ┆ GR_5_stars ┆ GR_pages ┆ GR_format │
│ ---           ┆ ---        ┆ ---                    ┆ ---       ┆   ┆ ---        ┆ ---        ┆ ---      ┆ ---       │
│ str           ┆ str        ┆ str                    ┆ f64       ┆   ┆ f64        ┆ f64        ┆ f64      ┆ str       │
╞═══════════════╪════════════╪════════════════════════╪═══════════╪═══╪════════════╪════════════╪══════════╪═══════════╡
│ 9788027153725 ┆ 2024-12-02 ┆ Zeptej se vědce:       ┆ 4.0       ┆ … ┆ 1.0        ┆ 1.0        ┆ 264.0    ┆ paperback │
│               ┆ 23:19:11   ┆ Neexistují bl…         ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788076333680 ┆ 2024-12-02 ┆ Bouře nad savanou by   ┆ 4.0       ┆ … ┆ 2.0        ┆ 0.0        ┆ 216.0    ┆ hardcover │
│               ┆ 23:54:30   ┆ Hana Hind…             ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788000060019 ┆ 2024-12-03 ┆ Vire, padni! by Ivona  ┆ 4.25      ┆ … ┆ 0.0        ┆ 3.0        ┆ 168.0    ┆ hardcover │
│               ┆ 01:06:20   ┆ Březinov…              ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788076660793 ┆ 2024-12-03 ┆ Stříbrná princezna by  ┆ 4.0       ┆ … ┆ 3.0        ┆ 1.0        ┆ 216.0    ┆ paperback │
│               ┆ 02:55:01   ┆ Kateřina…              ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788075511744 ┆ 2024-12-03 ┆ Když jsme se potkali   ┆ 3.0       ┆ … ┆ 0.0        ┆ 0.0        ┆ 224.0    ┆ hardcover │
│               ┆ 01:59:19   ┆ by Viktor…             ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788087595954 ┆ 2024-12-03 ┆ 4. Dobrodružství       ┆ 3.67      ┆ … ┆ 3.0        ┆ 2.0        ┆ 88.0     ┆ hardcover │
│               ┆ 02:58:11   ┆ pavouka Čendy…         ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788076111226 ┆ 2024-12-03 ┆ Gazely by Patrik Hartl ┆ 3.68      ┆ … ┆ 227.0      ┆ 127.0      ┆ 441.0    ┆ paperback │
│               ┆ 03:03:09   ┆                        ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788026449997 ┆ 2024-11-12 ┆ Ájurvéda & jóga pro    ┆ 4.2       ┆ … ┆ 2.0        ┆ 2.0        ┆ null     ┆ null      │
│               ┆ 00:31:39   ┆ ženy by Zu…            ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788076339651 ┆ 2024-12-03 ┆ Poslední Přemyslovna:  ┆ 1.0       ┆ … ┆ 0.0        ┆ 0.0        ┆ 264.0    ┆ hardcover │
│               ┆ 04:40:37   ┆ Vzdor a …              ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788011038410 ┆ 2024-12-03 ┆ Zpronevěra by Jindřich ┆ 1.0       ┆ … ┆ 0.0        ┆ 0.0        ┆ 280.0    ┆ hardcover │
│               ┆ 03:09:58   ┆ Husička                ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788075685643 ┆ 2024-12-03 ┆ Hadí královna by       ┆ 3.75      ┆ … ┆ 1.0        ┆ 1.0        ┆ 460.0    ┆ hardcover │
│               ┆ 04:02:15   ┆ Zuzana Štorko…         ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788076391307 ┆ 2024-12-03 ┆ Na kočičí svědomí by   ┆ 2.5       ┆ … ┆ 1.0        ┆ 0.0        ┆ 260.0    ┆ hardcover │
│               ┆ 03:04:48   ┆ Markéta H…             ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788075885227 ┆ 2024-12-03 ┆ Hvězda mého života     ┆ 3.69      ┆ … ┆ 3.0        ┆ 5.0        ┆ 409.0    ┆ hardcover │
│               ┆ 00:40:57   ┆ (Arkádie, #…           ┆           ┆   ┆            ┆            ┆          ┆           │
│ 9788076500983 ┆ 2024-12-03 ┆ Veškárničky by Martina ┆ 0.0       ┆ … ┆ 0.0        ┆ 0.0        ┆ 80.0     ┆ hardcover │
│               ┆ 01:59:29   ┆ Pospíši…               ┆           ┆   ┆            ┆            ┆          ┆ 

In [735]:
dk

shape: (6_854, 16)
┌───────────────┬───────────────┬──────────────┬───────────┬───┬──────────────┬──────────────┬──────────────┬──────────┐
│ DK_isbn       ┆ DK_date       ┆ DK_titul     ┆ DK_rating ┆ … ┆ DK_dalších_s ┆ DK_Doporučen ┆ DK_autorstvo ┆ DK_vyslo │
│ ---           ┆ ---           ┆ ---          ┆ ---       ┆   ┆ eznamech     ┆ ých          ┆ ---          ┆ ---      │
│ str           ┆ str           ┆ str          ┆ f64       ┆   ┆ ---          ┆ ---          ┆ str          ┆ f64      │
│               ┆               ┆              ┆           ┆   ┆ f64          ┆ f64          ┆              ┆          │
╞═══════════════╪═══════════════╪══════════════╪═══════════╪═══╪══════════════╪══════════════╪══════════════╪══════════╡
│ 9788011051204 ┆ 2024-12-02    ┆ Dubánek a    ┆ 90.0      ┆ … ┆ 2.0          ┆ null         ┆ ['Klára      ┆ 2024.0   │
│               ┆ 23:22:39      ┆ tajný vzkaz  ┆           ┆   ┆              ┆              ┆ Smolíková']  ┆          │
│ 9788027801909 ┆ 2024-12-02    ┆ Masomlejnek: ┆ 94.0      ┆ … ┆ 1.0          ┆ 1.0          ┆ ['Honza      ┆ 2024.0   │
│               ┆ 23:19:53      ┆ Srab         ┆           ┆   ┆              ┆              ┆ Slívka']     ┆          │
│ 9788072155910 ┆ 2024-12-02    ┆ Lidský los   ┆ 90.0      ┆ … ┆ null         ┆ null         ┆ ['Jan        ┆ 2020.0   │
│               ┆ 22:42:36      ┆              ┆           ┆   ┆              ┆              ┆ Vladislav']  ┆          │
│ 9788087373019 ┆ 2024-12-02    ┆ Hledání      ┆ 100.0     ┆ … ┆ null         ┆ null         ┆ ['Sebastian  ┆ 2023.0   │
│               ┆ 23:36:52      ┆ střední      ┆           ┆   ┆              ┆              ┆ Prax']       ┆          │
│               ┆               ┆ cesty        ┆           ┆   ┆              ┆              ┆              ┆          │
│ 9788072952823 ┆ 2024-12-02    ┆ Jmenuji se   ┆ 78.0      ┆ … ┆ null         ┆ null         ┆ ['Antonín    ┆ 2021.0   │
│               ┆ 23:37:39      ┆ Marie        ┆           ┆   ┆              ┆              ┆ Randa']      ┆          │
│ 9788024287904 ┆ 2024-11-12    ┆ Zapomenuté   ┆ 82.0      ┆ … ┆ null         ┆ 1.0          ┆ ['Martin     ┆ null     │
│               ┆ 02:16:11      ┆ osudy,       ┆           ┆   ┆              ┆              ┆ Brabec']     ┆          │
│               ┆               ┆ zločiny a    ┆           ┆   ┆              ┆              ┆              ┆          │
│               ┆               ┆ ta…          ┆           ┆   ┆              ┆              ┆              ┆          │
│ 9788090924536 ┆ 2024-12-02    ┆ Jasnou       ┆ 0.0       ┆ … ┆ null         ┆ null         ┆ ['Marek      ┆ 2024.0   │
│               ┆ 22:41:53      ┆ cestou: 7    ┆           ┆   ┆              ┆              ┆ Hladík',     ┆          │
│               ┆               ┆ kroků k      ┆           ┆   ┆              ┆              ┆ 'Vít Aora']  ┆          │
│               ┆               ┆ novém…       ┆           ┆   ┆              ┆              ┆              ┆          │
│ 9788027117048 ┆ 2024-12-02    ┆ Babiččina    ┆ 91.0      ┆ … ┆ 2.0          ┆ 1.0          ┆ ['Sandra     ┆ 2020.0   │
│               ┆ 22:46:17      ┆ kouzelná     ┆           ┆   ┆              ┆              ┆ Dražilová    ┆          │
│               ┆               ┆ zahrádka     ┆           ┆   ┆              ┆              ┆ Zlámalová']  ┆          │
│ 9788027801114 ┆ 2024-12-02    ┆ Camino del   ┆ 80.0      ┆ … ┆ null         ┆ null         ┆ ['Ondřej     ┆ 2024.0   │
│               ┆ 22:48:58      ┆ Norte        ┆           ┆   ┆              ┆              ┆ Šebesta']    ┆          │
│ 9788090732582 ┆ 2024-12-02    ┆ Sarajevo     ┆ 65.0      ┆ … ┆ null         ┆ null         ┆ ['Milan      ┆ 2020.0   │
│               ┆ 23:05:10      ┆              ┆           ┆   ┆              ┆              ┆ Holub']      ┆          │
│ 9788090748422 ┆ 2024-12-02    ┆ Freud a      ┆ 73.0      ┆ … ┆ null         ┆ null         ┆ ['Evžen      ┆

In [737]:
df_gr = df_isbn.join(gr, left_on='isbn', right_on='GR_isbn',how='right')
df_gr.sample(10)

shape: (10, 89)
┌──────────┬────────────────────────┬───────────────┬───────────┬───┬────────────┬────────────┬──────────┬───────────┐
│ 100_ind1 ┆ 100_a                  ┆ 100_7         ┆ 100_4     ┆ … ┆ GR_4_stars ┆ GR_5_stars ┆ GR_pages ┆ GR_format │
│ ---      ┆ ---                    ┆ ---           ┆ ---       ┆   ┆ ---        ┆ ---        ┆ ---      ┆ ---       │
│ str      ┆ str                    ┆ str           ┆ list[str] ┆   ┆ f64        ┆ f64        ┆ f64      ┆ str       │
╞══════════╪════════════════════════╪═══════════════╪═══════════╪═══╪════════════╪════════════╪══════════╪═══════════╡
│ 1        ┆ Lukačovičová, Lucie,   ┆ jo2004232808  ┆ ["aut"]   ┆ … ┆ 23.0       ┆ 12.0       ┆ 320.0    ┆ paperback │
│ 1        ┆ Pilátová, Markéta,     ┆ js20051031017 ┆ ["aut"]   ┆ … ┆ 0.0        ┆ 1.0        ┆ 32.0     ┆ hardcover │
│ 1        ┆ Krejčík, Přemysl,      ┆ xx0197400     ┆ ["aut"]   ┆ … ┆ 8.0        ┆ 4.0        ┆ 328.0    ┆ paperback │
│ 1        ┆ Krolupperová, Daniela, ┆ xx0012658     ┆ ["aut"]   ┆ … ┆ 5.0        ┆ 3.0        ┆ 56.0     ┆ hardcover │
│ 1        ┆ Maxa, David,           ┆ osa2014852329 ┆ ["aut"]   ┆ … ┆ 4.0        ┆ 2.0        ┆ null     ┆ null      │
│ 1        ┆ Augustová, Zuzana,     ┆ xx0009513     ┆ ["aut"]   ┆ … ┆ 0.0        ┆ 0.0        ┆ 228.0    ┆ hardcover │
│ 1        ┆ Král, Tomáš,           ┆ jo20211116244 ┆ ["aut"]   ┆ … ┆ 1.0        ┆ 0.0        ┆ 360.0    ┆ hardcover │
│ 1        ┆ Šlechtová, Hana,       ┆ xx0277666     ┆ ["aut"]   ┆ … ┆ 3.0        ┆ 2.0        ┆ 176.0    ┆ paperback │
│ 1        ┆ Hlasová, Blažena,      ┆ xx0313592     ┆ ["aut"]   ┆ … ┆ 0.0        ┆ 1.0        ┆ 160.0    ┆ hardcover │
│ 1        ┆ Bendová, Veronika,     ┆ xx0164195     ┆ ["aut"]   ┆ … ┆ 0.0        ┆ 2.0        ┆ 192.0    ┆ hardcover │
└──────────┴────────────────────────┴───────────────┴───────────┴───┴────────────┴────────────┴──────────┴───────────┘

In [741]:
df_dk = df_isbn.join(dk, left_on='isbn', right_on='DK_isbn',how='right')
df_dk.sample(10)

shape: (10, 91)
┌──────────┬────────────────┬───────────────┬───────────┬───┬───────────────┬───────────────┬───────────────┬──────────┐
│ 100_ind1 ┆ 100_a          ┆ 100_7         ┆ 100_4     ┆ … ┆ DK_dalších_se ┆ DK_Doporučený ┆ DK_autorstvo  ┆ DK_vyslo │
│ ---      ┆ ---            ┆ ---           ┆ ---       ┆   ┆ znamech       ┆ ch            ┆ ---           ┆ ---      │
│ str      ┆ str            ┆ str           ┆ list[str] ┆   ┆ ---           ┆ ---           ┆ str           ┆ f64      │
│          ┆                ┆               ┆           ┆   ┆ f64           ┆ f64           ┆               ┆          │
╞══════════╪════════════════╪═══════════════╪═══════════╪═══╪═══════════════╪═══════════════╪═══════════════╪══════════╡
│ 1        ┆ Hátlová,       ┆ xx0209027     ┆ ["aut"]   ┆ … ┆ null          ┆ null          ┆ ['Petra       ┆ 2023.0   │
│          ┆ Petra,         ┆               ┆           ┆   ┆               ┆               ┆ Hátlová']     ┆          │
│ 1        ┆ An, Elen,      ┆ xx0254907     ┆ ["aut"]   ┆ … ┆ 1.0           ┆ 6.0           ┆ ['Elen An']   ┆ 2020.0   │
│ 1        ┆ Serres,        ┆ mzk2002105282 ┆ ["aut",   ┆ … ┆ null          ┆ null          ┆ ['Michel      ┆ 2024.0   │
│          ┆ Michel,        ┆               ┆ "ive"]    ┆   ┆               ┆               ┆ Serres',      ┆          │
│          ┆                ┆               ┆           ┆   ┆               ┆               ┆ 'Bruno Latou… ┆          │
│ 1        ┆ Klíma,         ┆ jk01060531    ┆ ["aut"]   ┆ … ┆ 3.0           ┆ 23.0          ┆ ['Ladislav    ┆ 2021.0   │
│          ┆ Ladislav,      ┆               ┆           ┆   ┆               ┆               ┆ Klíma']       ┆          │
│ 1        ┆ Kalivoda,      ┆ mzk2023118197 ┆ ["aut",   ┆ … ┆ null          ┆ null          ┆ ['Ondřej      ┆ 2024.0   │
│          ┆ Ondřej,        ┆ 4             ┆ "pbl"]    ┆   ┆               ┆               ┆ Kalivoda']    ┆          │
│ 1        ┆ Jarchovský,    ┆ xx0098781     ┆ ["aut"]   ┆ … ┆ null          ┆ null          ┆ ['Zdeněk      ┆ 2021.0   │
│          ┆ Zdeněk,        ┆               ┆           ┆   ┆               ┆               ┆ Jarchovský',  ┆          │
│          ┆                ┆               ┆           ┆   ┆               ┆               ┆ '* antol…     ┆          │
│ 1        ┆ Šimek, Štěpán, ┆ osa2014825404 ┆ ["aut"]   ┆ … ┆ null          ┆ null          ┆ ['Štěpán      ┆ 2022.0   │
│          ┆                ┆               ┆           ┆   ┆               ┆               ┆ Šimek']       ┆          │
│ 1        ┆ Pšeničková-Sla ┆ xx0110238     ┆ ["aut"]   ┆ … ┆ null          ┆ null          ┆ ['Zdenka      ┆ 2020.0   │
│          ┆ víková, Zdena, ┆               ┆           ┆   ┆               ┆               ┆ Pšeničková    ┆          │
│          ┆                ┆               ┆           ┆   ┆               ┆               ┆ Slavíková'…   ┆          │
│ 1        ┆ Hrabal, Ondřej ┆ xx0213423     ┆ ["aut"]   ┆ … ┆ null          ┆ null          ┆ ['Ondřej      ┆ null     │
│          ┆ L.,            ┆               ┆           ┆   ┆               ┆               ┆ Hrabal']      ┆          │
│ 1        ┆ Březina, Jiří, ┆ xx0114321     ┆ ["aut"]   ┆ … ┆ 3.0           ┆ 25.0          ┆ ['Jiří        ┆ 2022.0   │
│          ┆                ┆               ┆           ┆   ┆               ┆               ┆ Březina']     ┆          │
└──────────┴────────────────┴───────────────┴───────────┴───┴───────────────┴───────────────┴───────────────┴──────────┘

In [763]:
df_dk.drop_nulls(subset=["DK_vyslo"]).sort(by="DK_vyslo").head()

shape: (5, 91)
┌──────────┬────────────────┬───────────────┬───────────┬───┬───────────────┬───────────────┬───────────────┬──────────┐
│ 100_ind1 ┆ 100_a          ┆ 100_7         ┆ 100_4     ┆ … ┆ DK_dalších_se ┆ DK_Doporučený ┆ DK_autorstvo  ┆ DK_vyslo │
│ ---      ┆ ---            ┆ ---           ┆ ---       ┆   ┆ znamech       ┆ ch            ┆ ---           ┆ ---      │
│ str      ┆ str            ┆ str           ┆ list[str] ┆   ┆ ---           ┆ ---           ┆ str           ┆ f64      │
│          ┆                ┆               ┆           ┆   ┆ f64           ┆ f64           ┆               ┆          │
╞══════════╪════════════════╪═══════════════╪═══════════╪═══╪═══════════════╪═══════════════╪═══════════════╪══════════╡
│ 1        ┆ Střihavková,   ┆ xx0248886     ┆ ["aut"]   ┆ … ┆ null          ┆ null          ┆ ['Viktor      ┆ 1984.0   │
│          ┆ Eva,           ┆               ┆           ┆   ┆               ┆               ┆ Faktor']      ┆          │
│ 1        ┆ Kopřiva,       ┆ ola200204863  ┆ ["aut"]   ┆ … ┆ null          ┆ 1.0           ┆ ['Tomáš       ┆ 2010.0   │
│          ┆ Tomáš,         ┆               ┆           ┆   ┆               ┆               ┆ Kopřiva']     ┆          │
│ 1        ┆ Lišková,       ┆ jn20001227108 ┆ ["aut"]   ┆ … ┆ null          ┆ null          ┆ ['Ludmila     ┆ 2014.0   │
│          ┆ Vlasta,        ┆               ┆           ┆   ┆               ┆               ┆ Klukanová']   ┆          │
│ 1        ┆ Vondruška,     ┆ xx0004129     ┆ ["aut"]   ┆ … ┆ 2.0           ┆ 21.0          ┆ ['Vlastimil   ┆ 2018.0   │
│          ┆ Vlastimil,     ┆               ┆           ┆   ┆               ┆               ┆ Vondruška']   ┆          │
│ 1        ┆ Kašpárek,      ┆ jx20100301005 ┆ ["aut"]   ┆ … ┆ 1.0           ┆ 9.0           ┆ ['Michal      ┆ 2018.0   │
│          ┆ Michal,        ┆               ┆           ┆   ┆               ┆               ┆ Kašpárek']    ┆          │
└──────────┴────────────────┴───────────────┴───────────┴───┴───────────────┴───────────────┴───────────────┴──────────┘

In [743]:
df_gr_graf = df_gr.filter(pl.col('GR_isbn').is_in(romany_isbn)).filter(pl.col("GR_rating") >= 0).filter(pl.col('GR_ratings_count') >= 5).filter(pl.col("stran") > 30)

In [745]:
gr_scatter = alt.Chart(
    alt_friendly(df_gr_graf),
    width=120
).mark_point(size=1, color='#81A9D5').encode(
    alt.X("stran:Q", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
    alt.Y("GR_rating:Q", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6'))
)

# Add regression line
gr_regression = alt.Chart(
    alt_friendly(df_gr_graf)
).transform_regression(
    'stran', 'GR_rating', method="linear"
).mark_line(color='#445B78').encode(
    alt.X("stran:Q", title="počet stran", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
    alt.Y("GR_rating:Q", title="hodnocení na Goodreads", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6'))
)

# Combine the plots
gr_final_chart = gr_scatter + gr_regression

gr_final_chart

alt.LayerChart(...)

In [663]:
df_dk_graf = df_dk.filter(pl.col('DK_isbn').is_in(romany_isbn)).filter(pl.col("DK_rating") >= 0).filter(pl.col('DK_ratings_count') >= 5).filter(pl.col("stran") > 30)

In [747]:
dk_scatter = alt.Chart(
    alt_friendly(df_dk_graf),

    width=120
).mark_point(size=1, color='#81A9D5').encode(
    alt.X("stran:Q"),
    alt.Y("DK_rating:Q")
)

# Add regression line
dk_regression = alt.Chart(
    alt_friendly(df_dk_graf)
).transform_regression(
    'stran', 'DK_rating'
).mark_line(color='#445B78').encode(
    alt.X("stran:Q", title="počet stran", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
    alt.Y("DK_rating:Q", title="hodnocení na Databázi knih", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6'))
)

# Combine the plots
dk_final_chart = (dk_scatter + dk_regression)

dk_final_chart

alt.LayerChart(...)

In [749]:
len(df_gr_graf)

859

In [751]:
len(df_dk_graf)

614

In [767]:
alt.concat(gr_final_chart, dk_final_chart).properties(
    title=alt.Title("Dlouhým příběhům dáváme víc hvězdiček", subtitle=["Hodnocení současných českých románů na","čtenářských platformách Goodreads a Databáze knih"])
)

alt.ConcatChart(...)